In [1]:
import pyodbc, os, json, csv
from datetime import datetime

In [2]:
# 루트폴더 지정
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
with open(os.path.join(path_root, 'configs', 'config_revised.json'), 'r') as config_file:
    config = json.load(config_file)

display(config)

starting_time = datetime.now()

# 주요 폴더 경로 지정
paths = config['paths']
path_tables = os.path.join(path_root, *paths['tables'])
# path_results = os.path.join(path_root, *paths['results'])

print(path_tables)
# print(path_results)

{'connection_info': {'DSNNAME': 'Tibero6',
  'DBUSER': 'snits',
  'DBPWD': 'snitsUIspxmworks#PW'},
 'paths': {'data': ['Data'],
  'intermediates': ['Intermediates'],
  'results': ['Results'],
  'tables': ['Data', 'tables'],
  'networks': ['Data', 'networks'],
  'scripts': ['Scripts']}}

c:\github\siggen\Data\tables


In [3]:
config = {'connection_info': {'DSNNAME': 'Tibero6',
  'DBUSER': 'snits',
  'DBPWD': 'snitsUIspxmworks#PW'},
 'paths': {'data': ['Data'],
  'intermediates': ['Intermediates'],
  'results': ['Results'],
  'tables': ['Data', 'tables'],
  'networks': ['Data', 'networks'],
  'scripts': ['Scripts']}}

In [4]:
connection_info = config['connection_info']
DSNNAME = connection_info["DSNNAME"]
DBUSER = connection_info["DBUSER"]
DBPWD = connection_info["DBPWD"]
cnxn = pyodbc.connect(f'DSN={DSNNAME};UID={DBUSER};PWD={DBPWD};charset=utf-8')
cursor = cnxn.cursor()

In [5]:
# 스키마 및 테이블명
schema = 'SNMS'
tables = ['TC_IF_TOD_DAY_PLAN', # TOD 일계획 현황#
          'TC_IF_TOD_HOLIDAY_PLAN', # TOD 휴일 계획#
          'TC_IF_TOD_RED_YELLO', # TOD 적색 및 황색 시간#
          'TC_IF_TOD_WEEK_PLAN', # TOD 주 계획#
          # 'TL_IF_SIGL', # 신호 운영 이력
          'TL_IF_SIGL_CYCL', # 신호 운영 주기 이력#
          'TM_FA_CRSRD', # 교차로 마스터#
          'TN_IF_SIGL_FLOW', # 신호 현시 별 이동류 방향#
          ]

# 폴더 Data\tables\yyyymmdd_hhmmss 생성
timestamp = starting_time.strftime('%Y%m%d')
# base_dir = os.path.join(path_tables, timestamp)
os.makedirs(os.path.join(path_tables, timestamp), exist_ok=True)


In [6]:
from datetime import datetime, timedelta
end_dt = datetime(2024, 7, 17, 18, 0)
end_dt.strftime("%Y_%m%d_%H_%M_%S")

'2024_0717_18_00_00'

In [7]:
term_dt = '2024_0717_18_00_20'
term_DT = datetime.strptime(term_dt, '%Y_%m%d_%H_%M_%S')
init_DT = term_DT - timedelta(minutes=5)
init_dt = init_DT.strftime("%Y_%m%d_%H_%M_%S")
print(init_dt)
print(term_dt)
print(init_DT)
print(term_DT)

2024_0717_17_55_20
2024_0717_18_00_20
2024-07-17 17:55:20
2024-07-17 18:00:20


In [8]:
def fetch_table(table, condition=""):
    try:
        query = f"SELECT * FROM {schema}.{table} {condition}"
        cursor.execute(query)
        csv_file_path = os.path.join(path_tables, timestamp, f"{table}.csv")
        with open(csv_file_path, 'w', newline='', encoding='utf-8-sig') as csvfile:
            csv_writer = csv.writer(csvfile)
            columns = [column[0] for column in cursor.description]
            csv_writer.writerow(columns)
            for row in cursor.fetchall():
                csv_writer.writerow(row)
    except Exception as e:
        print(f"오류 발생: {e}")

In [9]:
for table in tables:
    print(table)
    fetch_table(table)

TC_IF_TOD_DAY_PLAN
TC_IF_TOD_HOLIDAY_PLAN
TC_IF_TOD_RED_YELLO
TC_IF_TOD_WEEK_PLAN
TL_IF_SIGL_CYCL
TM_FA_CRSRD
TN_IF_SIGL_FLOW


In [11]:
fetch_table('TL_IF_SIGL', condition="WHERE TRUNC(PHASE_DT) = TO_DATE('2024-07-29', 'YYYY-MM-DD') AND CRSRD_ID IN (436, 437, 438, 442, 443, 444, 455, 456, 457, 458)")

In [10]:
print("SELECT * FROM SNMS.TC_IF_TOD_DAY_PLAN")

SELECT * FROM SNMS.TC_IF_TOD_DAY_PLAN
